In [ ]:
import numpy as np

In [1]:
def init_params():
    W1 = np.random.rand(10,1024) - 0.5
    b1 = np.random.rand(10,1) - 0.5
    W2 = np.random.rand(61,10) - 0.5
    b2 = np.random.rand(61,1) - 0.5
    return W1, b1 , W2, b2
def ReLU(Z):
    return np.maximum(Z,0)
def softmax(Z):
    A = np.exp(Z) / sum(np.exp(Z))
    return A
def forward_prop(W1, b1, W2, b2, X):
    Z1 = W1.dot(X) + b1
    A1 = ReLU(Z1)
    Z2 = W2.dot(A1) + b2
    A2 = softmax(Z2)
    return Z1, A1, Z2, A2
def ReLU_deriv(Z):
    return Z > 0
def one_hot(Y):
    one_hot_Y = np.zeros((Y.size, Y.max() + 1))
    one_hot_Y[np.arange(Y.size), Y] = 1
    one_hot_Y = one_hot_Y.T
    return one_hot_Y
def backward_prop(Z1, A1, Z2, A2, W1, W2, X, Y):
    one_hot_Y = one_hot(Y)
    dZ2 = A2 - one_hot_Y
    dW2 = 1 / m * dZ2.dot(A1.T)
    db2 = 1 / m * np.sum(dZ2)
    dZ1 = W2.T.dot(dZ2) * ReLU_deriv(Z1)
    dW1 = 1 / m * dZ1.dot(X.T)
    db1 = 1 / m * np.sum(dZ1)
    return dW1, db1, dW2, db2
def update_params(W1, b1, W2, b2, dW1, db1, dW2, db2, alpha):
    W1 = W1 - alpha * dW1
    b1 = b1 - alpha * db1    
    W2 = W2 - alpha * dW2  
    b2 = b2 - alpha * db2    
    return W1, b1, W2, b2
def get_predictions(A2):
    return np.argmax(A2, 0)
def get_accuracy(predictions, Y):
    #print(predictions, Y)
    return np.sum(predictions == Y) / Y.size

In [2]:
import pandas as pd
#import data_ready as dr
import os
import struct
import numpy as np
from matplotlib import pyplot as plt 

'''
npz = np.load("weights.npz")
W1 = np.array(npz['arr_0'])
b1 = np.array(npz['arr_1'])
W2 = np.array(npz['arr_2'])
b2 = np.array(npz['arr_3'])
'''
def encode_image(X,W1,b1,W2,b2):
    current_image = X
    _, _, _, A2  = forward_prop(W1,b1,W2,b2,current_image)
    return A2
    #print(A2)
    #np.save('pred', A2)


### Load in The Weights

In [3]:
bt_npz = np.load("bt_weights.npz")
cr_npz = np.load("cr_weights.npz")
gt_npz = np.load("gt_weights.npz")

In [4]:
W1_bt = np.array(bt_npz['arr_0'])
b1_bt = np.array(bt_npz['arr_1'])
W2_bt = np.array(bt_npz['arr_2'])
b2_bt = np.array(bt_npz['arr_3'])

In [5]:
W1_cr = np.array(cr_npz['arr_0'])
b1_cr = np.array(cr_npz['arr_1'])
W2_cr = np.array(cr_npz['arr_2'])
b2_cr = np.array(cr_npz['arr_3'])

In [6]:
W1_gt = np.array(gt_npz['arr_0'])
b1_gt = np.array(gt_npz['arr_1'])
W2_gt = np.array(gt_npz['arr_2'])
b2_gt = np.array(gt_npz['arr_3'])

### Load in the Dataset

In [7]:
datac = pd.read_csv('cro_data_test.csv')
datac = np.array(datac)

m,n = datac.shape
data_trainc = datac[1000:m].T

Y_trainc = data_trainc[0].astype(int)
X_trainc = data_trainc[1:n]

current_image_c = X_trainc[:,1,None]

In [8]:
datag = pd.read_csv('gtsrb_data_test.csv')
datag = np.array(datag)

m,n = datag.shape
data_traing = datag[1000:m].T

Y_traing = data_traing[0].astype(int)
X_traing = data_traing[1:n]

current_image_g = X_traing[:,1,None]

In [9]:
datab = pd.read_csv('bel_data_test.csv')
datab = np.array(datab)

m,n = datab.shape
data_trainb = datab[1000:m].T

Y_trainb = data_trainb[0].astype(int)
X_trainb = data_trainb[1:n]

current_image_b = X_trainc[:,1,None]

# Encoding 1 Image

In [10]:
c1 = encode_image(current_image_c,W1_cr,b1_cr,W2_cr,b2_cr)

In [11]:
b1 = encode_image(current_image_b,W1_bt,b1_bt,W2_bt,b2_bt)

In [12]:
g1 = encode_image(current_image_g,W1_gt,b1_gt,W2_gt,b2_gt)

In [13]:
np.save('data/Single_Encoding/pred_c', c1)
np.save('data/Single_Encoding/pred_b', b1)
np.save('data/Single_Encoding/pred_g', g1)

# Encoding 900 Images

In [44]:
for x in range(0,900):
    current_image_g = X_traing[:,x,None]
    g1 = encode_image(current_image_g,W1_gt,b1_gt,W2_gt,b2_gt)
    np.save('data/9_G/pred_g' + str(x), g1)

In [45]:
for x in range(0,900):
    current_image_b = X_trainb[:,x,None]
    b1 = encode_image(current_image_b,W1_bt,b1_bt,W2_bt,b2_bt)
    np.save('data/9_B/pred_b' + str(x), b1)

In [46]:
for x in range(0,900):
    current_image_c = X_trainc[:,x,None]
    c1 = encode_image(current_image_c,W1_cr,b1_cr,W2_cr,b2_cr)
    np.save('data/9_C/pred_c' + str(x), c1)

Encoding 1800 Images

In [47]:
for x in range(0,1800):
    current_image_g = X_traing[:,x,None]
    g1 = encode_image(current_image_g,W1_gt,b1_gt,W2_gt,b2_gt)
    np.save('data/18_G/pred_g' + str(x), g1)

In [48]:
for x in range(0,1800):
    current_image_b = X_trainb[:,x,None]
    b1 = encode_image(current_image_b,W1_bt,b1_bt,W2_bt,b2_bt)
    np.save('data/18_B/pred_b' + str(x), b1)

In [49]:
for x in range(0,1800):
    current_image_c = X_trainc[:,x,None]
    c1 = encode_image(current_image_c,W1_cr,b1_cr,W2_cr,b2_cr)
    np.save('data/18_C/pred_c' + str(x), c1)